In [1]:
import pandas as pd
from scipy import stats
import numpy as np

data='../3classdata/W/1.csv'
window=3
resolution=500
shift=3

import glob
from functools import partial
    

In [2]:
def gaussian_interval(resolution):
    # use a gaussian distribution, mean 0, std deviation 0.25
    distribution = stats.norm(loc=0, scale=0.25)
    # bounds of range for inverse comulative distribution function
    bounds = distribution.cdf([-1, 1])
    # generate linear space of 2*resolution points using bounds
    linsp = np.linspace(*bounds, num=2*resolution)
    # obtain the array of 2*resolution points
    return distribution.ppf(linsp)
gaussian_interval(20)

array([-1.        , -0.48715223, -0.40806948, -0.3564728 , -0.31673373,
       -0.28370106, -0.25499594, -0.22931092, -0.20584419, -0.18406497,
       -0.16360107, -0.14417942, -0.1255919 , -0.10767457, -0.09029443,
       -0.07334053, -0.05671771, -0.04034218, -0.02413812, -0.00803494,
        0.00803494,  0.02413812,  0.04034218,  0.05671771,  0.07334053,
        0.09029443,  0.10767457,  0.1255919 ,  0.14417942,  0.16360107,
        0.18406497,  0.20584419,  0.22931092,  0.25499594,  0.28370106,
        0.31673373,  0.3564728 ,  0.40806948,  0.48715223,  1.        ])

In [3]:
df = pd.read_csv(data, dtype=float, header=None)
# rotate dataframe (each column is a temporal sequence)
df = df.T.reset_index().reindex(axis=1).drop(['index'], axis=1).infer_objects()


In [4]:
df = ((df - df.min()) / (df.max() - df.min()))*2 - 1
df.head()

0         1         2         3         4         5         6   \
0 -0.794245 -1.000000  0.828071 -0.994168  0.944798  0.668407 -0.373019   
1 -0.773646 -0.982051  0.838096 -1.000000  0.702760  0.490809 -0.536255   
2 -0.704494 -0.941707  0.867532 -0.971583  0.515924  0.189991 -0.667524   
3 -0.702488 -0.727678  0.847612 -0.956749  0.222930 -0.078956 -0.759538   
4 -0.653693 -0.474916  0.893637 -0.896301 -0.210191 -0.359162 -0.840516   

         7         8         9         10        11        12        13  \
0 -0.150670  0.847187  0.993011  0.997649  0.424828  0.707602 -0.548011   
1  0.522335  0.949622  1.000000  1.000000  0.416761  0.719298 -0.696552   
2  0.557023  0.946264  0.940591  0.540661 -0.131239  0.754386 -0.875862   
3  0.573242  0.914358  0.871396 -0.152875 -0.246231  0.766082 -0.839788   
4 -1.000000  0.993283  0.808842 -0.618419 -0.535811  0.812865 -0.818568   

         14        15        16        17        18        19  
0 -0.897720 -0.996191  0.733333  1.000000 -1.000000 -1.000000  
1 -0.840543 -1.000000  0.721212  0.707079 -0.989454 -0.998286  
2 -0.722166 -0.990737  0.715152  0.664768 -0.700204 -0.977304  
3 -0.739604 -0.937756  0.660606  0.243287 -0.358765 -0.947124  
4 -0.519115 -0.823284  0.630303  0.222132 -0.169913 -0.810559

In [5]:
#df = df.apply(partial(
   # discretize_series, gaussianInterval=gaussian_interval(resolution)))
#df.head()

In [6]:
l = df.apply(lambda x : pd.cut(x, gaussian_interval(resolution), right=True).apply(lambda l : l.left))
r = df.apply(lambda x : pd.cut(x, gaussian_interval(resolution), right=True).apply(lambda l : l.right))

In [7]:
df = l

In [8]:
df

0        1         2        3         4        5        6        7   \
0  -1.0000 -1.00000  0.770200 -1.00000  0.770200  0.66230 -0.37440 -0.15070   
1  -1.0000 -1.00000  0.770200 -1.00000  0.686000  0.48980 -0.54220  0.51840   
2  -0.7182 -1.00000  0.770200 -1.00000  0.513200  0.18950 -0.68600  0.55620   
3  -0.7182 -0.77020  0.770200 -1.00000  0.222100 -0.07941 -0.77020  0.57220   
4  -0.6623 -0.47750  0.770200 -1.00000 -0.210200 -0.35970 -1.00000 -1.00000   
5  -0.2886 -0.71820  0.770200 -0.77020 -0.010980 -0.44960 -1.00000  0.68600   
6  -0.1266 -0.37440  0.770200 -1.00000  0.180400 -0.60180 -1.00000  0.03936   
7   0.1614 -0.04573  0.662300 -0.77020  0.302500 -0.71820 -1.00000 -0.09406   
8   0.4941  0.24950  0.386400 -0.62750 -0.036190 -0.77020 -1.00000  0.11460   
9   0.5081  0.54220  0.179600 -0.27560 -0.513200 -1.00000 -1.00000  0.45600   
10  0.6018  0.44340  0.001568 -0.27910 -0.494100 -1.00000 -1.00000  0.71820   
11  0.6623  0.37830 -0.198800 -0.02671 -0.518400 -1.00000 -1.00000  0.77020   
12  0.7702  0.66230 -0.408600  0.17800 -0.326000 -1.00000 -1.00000  0.64330   
13  0.7702  0.77020 -0.294800  0.52970  0.235400 -1.00000 -1.00000  0.39710   
14  0.7702  0.77020 -0.225800  0.77020  0.601800 -1.00000 -1.00000  0.30120   
15  0.7702  0.77020 -0.613800  0.77020  0.718200 -1.00000 -1.00000  0.27910   
16  0.7702  0.77020 -1.000000  0.77020  0.770200 -1.00000 -1.00000  0.39060   
17  0.7702  0.71820 -1.000000  0.77020  0.770200 -1.00000 -1.00000  0.61380   
18  0.7702  0.62750 -1.000000  0.77020  0.770200 -0.66230 -1.00000  0.77020   
19  0.7702  0.52400 -1.000000  0.77020  0.354500 -0.47750 -1.00000  0.77020   
20  0.7702  0.44040 -1.000000  0.77020  0.001568 -0.24130 -1.00000  0.77020   
21  0.7702  0.57220 -1.000000  0.77020 -0.202300 -0.08404 -1.00000  0.77020   
22  0.7702  0.64330 -1.000000  0.77020 -0.240300  0.21290 -1.00000  0.71820   
23  0.7702  0.71820 -1.000000  0.45940 -0.181200  0.31880 -1.00000  0.64330   
24  0.7702  0.71820 -1.000000  0.44640  0.001568  0.48560 -0.34290  0.50330   
25  0.6623  0.77020 -1.000000  0.27790  0.247400  0.61380  0.19200  0.45280   
26  0.2622  0.77020 -1.000000  0.12230  0.374400  0.71820  0.47000  0.43750   
27  0.2464  0.77020 -1.000000 -0.09138  0.485600  0.77020  0.71820  0.41590   
28 -0.2239  0.66230 -1.000000 -0.14330  0.415900  0.77020  0.77020  0.37640   
29 -0.3494  0.56390 -0.718200 -0.26110  0.277900  0.77020  0.77020  0.36880   
30 -0.7702  0.33660 -0.643300 -0.29480 -0.048920  0.77020  0.77020  0.33350   
31 -1.0000  0.36150 -0.459400 -0.31880 -0.202300  0.77020  0.77020  0.33500   
32 -1.0000  0.20750 -0.386400 -0.37060 -0.542200  0.77020  0.77020  0.33660   
33 -1.0000  0.08073 -0.170800 -0.37640 -0.591000  0.77020  0.55620  0.30910   
34 -1.0000  0.09947 -0.007214 -0.38030 -0.718200  0.77020  0.05598  0.27440   
35 -1.0000 -0.25360  0.120200 -0.38030 -1.000000  0.77020 -0.44340  0.27330   
36 -1.0000 -0.21200  0.293600 -0.38030 -1.000000  0.77020 -0.44960  0.26430   
37 -1.0000 -0.29360  0.317400 -0.39060 -1.000000  0.77020 -0.64330  0.24740   
38 -1.0000 -0.36690  0.318800 -0.39280 -1.000000  0.77020 -0.62750  0.22300   
39 -1.0000 -0.34940  0.380300 -0.40160 -1.000000  0.77020 -0.71820  0.20670   

         8        9       10        11      12        13       14       15  \
0   0.77020  0.77020  0.7702  0.423700  0.6860 -0.549000 -1.00000 -1.00000   
1   0.77020  0.77020  0.7702  0.415900  0.7182 -0.718200 -1.00000 -1.00000   
2   0.77020  0.77020  0.5358 -0.131600  0.7182 -1.000000 -0.77020 -1.00000   
3   0.77020  0.77020 -0.1530 -0.246400  0.7182 -1.000000 -0.77020 -1.00000   
4   0.77020  0.77020 -0.6275 -0.535800  0.7702 -1.000000 -0.52400 -1.00000   
5   0.77020  0.71820 -0.7182 -0.503300  0.7702 -1.000000 -0.27670 -0.71820   
6   0.77020  0.60180 -1.0000 -1.000000  0.7702 -1.000000  0.07677 -0.64330   
7   0.77020  0.64330 -1.0000 -1.000000  0.7702 -1.000000  0.48980 -0.51840   
8   0.77020  0.66230 -0.6275 -1.000000  0.7702 -1.000000  0.77020 

In [25]:
def generate_words(col, w, s):
    word = []
    idx = 0
    distance = abs(w-s)
    while idx < len(col):
        if len(word) == w:
            yield word
            word = []
            if w < s and idx == w:
                idx += distance
            if w > s:
                idx -= distance 
        else:
            word.append(col[idx])
            idx+=1

In [27]:
for _,col in df.iteritems():
    print(list(generate_words(col, 3, 5)))

[[-1.0, -1.0, -0.7182], [-0.2886, -0.1266, 0.1614], [0.4941, 0.5081, 0.6018], [0.6623, 0.7702, 0.7702], [0.7702, 0.7702, 0.7702], [0.7702, 0.7702, 0.7702], [0.7702, 0.7702, 0.7702], [0.7702, 0.7702, 0.6623], [0.2622, 0.2464, -0.2239], [-0.3494, -0.7702, -1.0], [-1.0, -1.0, -1.0], [-1.0, -1.0, -1.0]]
[[-1.0, -1.0, -1.0], [-0.7182, -0.3744, -0.04573], [0.2495, 0.5422, 0.4434], [0.3783, 0.6623, 0.7702], [0.7702, 0.7702, 0.7702], [0.7182, 0.6275, 0.524], [0.4404, 0.5722, 0.6433], [0.7182, 0.7182, 0.7702], [0.7702, 0.7702, 0.6623], [0.5639, 0.3366, 0.3615], [0.2075, 0.08073, 0.09947], [-0.2536, -0.212, -0.2936]]
[[0.7702, 0.7702, 0.7702], [0.7702, 0.7702, 0.6623], [0.3864, 0.1796, 0.001568], [-0.1988, -0.4086, -0.2948], [-0.2258, -0.6138, -1.0], [-1.0, -1.0, -1.0], [-1.0, -1.0, -1.0], [-1.0, -1.0, -1.0], [-1.0, -1.0, -1.0], [-0.7182, -0.6433, -0.4594], [-0.3864, -0.1708, -0.007214], [0.1202, 0.2936, 0.3174]]
[[-1.0, -1.0, -1.0], [-0.7702, -1.0, -0.7702], [-0.6275, -0.2756, -0.2791], [-0.026